In [1]:
# !pip list

In [2]:
# !python3 -m pip install --upgrade pip

In [3]:
import numpy as np
from transformers import (
  HubertForCTC,
  Wav2Vec2Processor,
  Wav2Vec2CTCTokenizer,
  Wav2Vec2FeatureExtractor,
  TrainingArguments,
  Trainer,
)
import torch
from transformers import Wav2Vec2Processor
from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union
from datasets import load_metric, concatenate_datasets, load_dataset, Audio

/root/audio/mhubert/venv/lib/python3.10/site-packages/transformers/utils/hub.py:127: FutureWarning: Using `TRANSFORMERS_CACHE` is deprecated and will be removed in v5 of Transformers. Use `HF_HOME` instead.
  warnings.warn(


In [4]:
@dataclass
class DataCollatorCTCWithPadding:
  processor: Wav2Vec2Processor
  padding: Union[bool, str] = True

  def __call__(
    self, features: List[Dict[str, Union[List[int], torch.Tensor]]]
  ) -> Dict[str, torch.Tensor]:
    # split inputs and labels since they have to be of different lengths and need
    # different padding methods
    input_features = [{"input_values": feature["input_values"]} for feature in features]
    label_features = [{"input_ids": feature["labels"]} for feature in features]

    batch = self.processor.pad(
      input_features,
      padding=self.padding,
      return_tensors="pt",
    )
    with self.processor.as_target_processor():
      labels_batch = self.processor.pad(
        label_features,
        padding=self.padding,
        return_tensors="pt",
      )

    # replace padding with -100 to ignore loss correctly
    labels = labels_batch["input_ids"].masked_fill(
      labels_batch.attention_mask.ne(1), -100
    )

    batch["labels"] = labels
    return batch

In [10]:
from huggingface_hub import notebook_login, login

login("hf_token", True)

Token is valid (permission: write).
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [11]:
from datasets import load_dataset, load_metric, Audio

common_voice_train = load_dataset("mozilla-foundation/common_voice_17_0", "ba", split="train+validation",keep_in_memory=True, trust_remote_code=True, use_auth_token=True)
common_voice_test = load_dataset("mozilla-foundation/common_voice_17_0", "ba", split="test",keep_in_memory=True, trust_remote_code=True, use_auth_token=True)


/root/audio/mhubert/venv/lib/python3.10/site-packages/datasets/load.py:2554: FutureWarning: 'use_auth_token' was deprecated in favor of 'token' in version 2.14.0 and will be removed in 3.0.0.
You can remove this warning by passing 'token=<use_auth_token>' instead.
  warnings.warn(


Generating train split: 0 examples [00:00, ? examples/s]


Reading metadata...: 0it [00:00, ?it/s]
Reading metadata...: 14736it [00:00, 147352.76it/s]
Reading metadata...: 29699it [00:00, 148687.16it/s]
Reading metadata...: 44568it [00:00, 148554.45it/s]
Reading metadata...: 59463it [00:00, 148706.38it/s]
Reading metadata...: 74334it [00:00, 145886.45it/s]
Reading metadata...: 88932it [00:00, 144124.52it/s]
Reading metadata...: 103353it [00:00, 143464.01it/s]
Reading metadata...: 119180it [00:00, 145082.51it/s]


Generating validation split: 0 examples [00:00, ? examples/s]


Reading metadata...: 14495it [00:00, 147067.28it/s]


...


Reading metadata...: 493it [00:00, 128354.55it/s]


Generating invalidated split: 0 examples [00:00, ? examples/s]


Reading metadata...: 7960it [00:00, 143292.85it/s]


Generating validated split: 0 examples [00:00, ? examples/s]


Reading metadata...: 0it [00:00, ?it/s]
Reading metadata...: 15618it [00:00, 156171.96it/s]
Reading metadata...: 31737it [00:00, 159119.31it/s]
Reading metadata...: 47649it [00:00, 155583.00it/s]
Reading metadata...: 63217it [00:00, 152091.81it/s]
Reading metadata...: 78440it [00:00, 151895.76it/s]
Reading metadata...: 93638it [00:00, 151469.59it/s]
Reading metadata...: 108790it [00:00, 150521.49it/s]
Reading metadata...: 123846it [00:00, 149525.41it/s]
Reading metadata...: 138801it [00:00, 146779.51it/s]
Reading metadata...: 154009it [00:01, 148376.19it/s]
Reading metadata...: 168857it [00:01, 146840.37it/s]
Reading metadata...: 183550it [00:01, 145609.81it/s]
Reading metadata...: 209653it [00:01, 148701.85it/s]


In [12]:
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [ ]:
# !pip install "soundfile>=0.12.1" -U

In [13]:
# !pip list

In [14]:
show_random_elements(common_voice_train.remove_columns(["path"]), num_examples=10)

In [15]:
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�\'\«\»\–\—aijno]'

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, ' ', batch["sentence"]).lower()
    return batch

In [16]:
common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

Map:   0%|          | 0/133675 [00:00<?, ? examples/s]

Map:   0%|          | 0/14513 [00:00<?, ? examples/s]

In [17]:
import re
chars_to_remove_regex = {'й':'й','i':''}

def replace_bad_characters(batch):
    for k in chars_to_remove_regex:
        batch["sentence"] = re.sub(k, chars_to_remove_regex[k], batch["sentence"]).lower()
    return batch

In [18]:
common_voice_train = common_voice_train.map(replace_bad_characters)
common_voice_test = common_voice_test.map(replace_bad_characters)

Map:   0%|          | 0/133675 [00:00<?, ? examples/s]

Map:   0%|          | 0/14513 [00:00<?, ? examples/s]

In [19]:
# show_random_elements(common_voice_train.remove_columns(["path"]))

In [20]:
def replace_hatted_characters(batch):
    batch["sentence"] = re.sub('[я]', 'йа', batch["sentence"])
    batch["sentence"] = re.sub('[ю]', 'йу', batch["sentence"])
    batch["sentence"] = re.sub('[ё]', 'йо', batch["sentence"])
    batch["sentence"] = re.sub('[ъ]', '', batch["sentence"])
    batch["sentence"] = re.sub('[ь]', '', batch["sentence"])
    if 'е' in batch["sentence"]:
        words=batch["sentence"].split(' ')
        new_list=[]
        for word in words:
            if len(word)==0:
                continue
            new_word=word
            if word[0]=='е':
                new_word='йэ'+word[1:]
            new_word=re.sub('[е]', 'э', new_word)
            new_list.append(new_word)

        batch["sentence"] = " ".join(new_list)
        
    words=batch["sentence"].split(' ')
    while '' in words:
        words.remove('')
    
    batch["sentence"]=" ".join(words)
    
    return batch

In [21]:
common_voice_train = common_voice_train.map(replace_hatted_characters)
common_voice_test = common_voice_test.map(replace_hatted_characters)

Map:   0%|          | 0/133675 [00:00<?, ? examples/s]

Map:   0%|          | 0/14513 [00:00<?, ? examples/s]

In [22]:
def extract_all_chars(batch):
    all_text = " ".join(batch["sentence"])
    vocab = list(set(all_text))
    return {"vocab": [vocab], "all_text": [all_text]}

In [23]:
common_voice_train.column_names

['client_id',
 'path',
 'audio',
 'sentence',
 'up_votes',
 'down_votes',
 'age',
 'gender',
 'accent',
 'locale',
 'segment',
 'variant']

In [24]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

Map:   0%|          | 0/133675 [00:00<?, ? examples/s]

Map:   0%|          | 0/14513 [00:00<?, ? examples/s]

In [25]:
common_voice_train = common_voice_train.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_test = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))

In [26]:
# import IPython.display as ipd
# import numpy as np
# import random

# rand_int = random.randint(0, len(common_voice_train)-1)

# print(common_voice_train[rand_int]["sentence"])
# ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=True, rate=16000)

In [27]:
# rand_int = random.randint(0, len(common_voice_train)-1)

# print("Target text:", common_voice_train[rand_int]["sentence"])
# print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
# print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])

In [28]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [29]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
vocab_dict

{' ': 0,
 'а': 1,
 'б': 2,
 'в': 3,
 'г': 4,
 'д': 5,
 'ж': 6,
 'з': 7,
 'и': 8,
 'й': 9,
 'к': 10,
 'л': 11,
 'м': 12,
 'н': 13,
 'о': 14,
 'п': 15,
 'р': 16,
 'с': 17,
 'т': 18,
 'у': 19,
 'ф': 20,
 'х': 21,
 'ц': 22,
 'ч': 23,
 'ш': 24,
 'щ': 25,
 'ы': 26,
 'э': 27,
 'ғ': 28,
 'ҙ': 29,
 'ҡ': 30,
 'ң': 31,
 'ҫ': 32,
 'ү': 33,
 'һ': 34,
 'ә': 35,
 'ө': 36}

In [30]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

In [31]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

39

In [32]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

In [33]:
model_id = "utter-project/mHuBERT-147"
feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained(model_id)
tokenizer = Wav2Vec2CTCTokenizer("vocab.json", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

model = HubertForCTC.from_pretrained(
  model_id,
  attention_dropout=0.1,
  hidden_dropout=0.1,
  feat_proj_dropout=0.1,
  mask_time_prob=0.05,
  layerdrop=0.1,
  final_dropout=0.3,
  ctc_loss_reduction="mean",
  pad_token_id=processor.tokenizer.pad_token_id,
  vocab_size=len(processor.tokenizer),
)

model.freeze_feature_encoder()

preprocessor_config.json:   0%|          | 0.00/227 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.59k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/378M [00:00<?, ?B/s]

Some weights of HubertForCTC were not initialized from the model checkpoint at utter-project/mHuBERT-147 and are newly initialized: ['encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'encoder.pos_conv_embed.conv.parametrizations.weight.original1', 'lm_head.bias', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [34]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [35]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names, num_proc=1)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names, num_proc=1)

Map:   0%|          | 0/133675 [00:00<?, ? examples/s]

/root/audio/mhubert/venv/lib/python3.10/site-packages/transformers/models/wav2vec2/processing_wav2vec2.py:157: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(
IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [36]:
# from datasets import Dataset
# import pickle
# import os

# def prepare_item(item):
#     try:
#         audio = item["audio"]
        
#         # Process audio
#         input_values = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
#         input_length = len(input_values)
        
#         # Process text
#         with processor.as_target_processor():
#             labels = processor(item["sentence"]).input_ids
        
#         return {
#             "input_values": input_values,
#             "input_length": input_length,
#             "labels": labels
#         }
#     except Exception as e:
#         print(f"Error processing item: {e}")
#         return None

# def process_dataset(dataset):
#     processed_data = []
#     ind=0
#     for item in dataset:
#         ind+=1
#         if ind%1000==0:
#             print(ind)
#         processed_item = prepare_item(item)
#         if processed_item is not None:
#             processed_data.append(processed_item)
    
#     return Dataset.from_list(processed_data)

# def save_to_pickle(prefix, data, index):
#     filename = f"processed_dataset/{prefix}_{index}.pkl"
#     with open(filename, 'wb') as f:
#         pickle.dump(data, f)
#     print(f"Saved {len(data)} items to {filename}")

# def process_dataset(prefix, dataset):
#     processed_data = []
#     total_processed = 0
#     for index, item in enumerate(dataset, start=1):
#         if index % 1000 == 0:
#             print(f"Processed {index} items")
        
#         processed_item = prepare_item(item)
#         if processed_item is not None:
#             processed_data.append(processed_item)
#             total_processed += 1
        
#         if len(processed_data) == 1000:
#             save_to_pickle(prefix, processed_data, total_processed // 1000)
#             processed_data = []  # Clear the list after saving
    
#     # Save any remaining items
#     if processed_data:
#         save_to_pickle(prefix, processed_data, (total_processed // 1000) + 1)
    
#     print(f"Total processed items: {total_processed}")
#     return total_processed

# process_dataset("test", common_voice_test)
# process_dataset("train", common_voice_train)
# # # Process the dataset
# # common_voice_test = process_dataset(common_voice_test)
# # common_voice_train = process_dataset(common_voice_train)

In [37]:
# def load_processed_dataset(prefix, directory="processed_dataset"):
#     all_data = []
#     for filename in sorted(os.listdir(directory)):
#         if filename.startswith(f"{prefix}_") and filename.endswith(".pkl"):
#             with open(os.path.join(directory, filename), 'rb') as f:
#                 all_data.extend(pickle.load(f))
#     return Dataset.from_list(all_data)

# # Load test and train datasets
# common_voice_test = load_processed_dataset("test")


In [38]:
# common_voice_train = load_processed_dataset("train")

In [39]:
wer_metric = load_metric("wer", trust_remote_code=True)

def compute_metrics(pred):
  pred_logits = pred.predictions
  pred_ids = np.argmax(pred_logits, axis=-1)
  pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id
  pred_str = processor.batch_decode(pred_ids)
  # we do not want to group tokens when computing the metrics
  label_str = processor.batch_decode(pred.label_ids, group_tokens=False)
  wer = wer_metric.compute(predictions=pred_str, references=label_str)
  return {"wer": wer}

/tmp/ipykernel_3579461/1950979149.py:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  wer_metric = load_metric("wer", trust_remote_code=True)


In [43]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

training_args = TrainingArguments(
  output_dir="training",
  report_to="tensorboard",
  per_device_train_batch_size=32,
  per_device_eval_batch_size=4,
  eval_strategy="steps",
  num_train_epochs=60,
  fp16=False,
  save_steps=1000,
  eval_steps=1000,
  logging_steps=100,
  learning_rate=1e-5,
  adam_beta1=0.9,
  adam_beta2=0.98,
  adam_epsilon=1e-08,
  warmup_ratio=0.1,
  save_total_limit=5,
  push_to_hub=False,
  load_best_model_at_end=True,
)

trainer = Trainer(
  model=model,
  data_collator=data_collator,
  args=training_args,
  compute_metrics=compute_metrics,
  train_dataset=common_voice_train,
  eval_dataset=common_voice_test,
  tokenizer=processor.feature_extractor,
)

Detected kernel version 5.4.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [ ]:
trainer.train()

/root/audio/mhubert/venv/lib/python3.10/site-packages/transformers/models/wav2vec2/processing_wav2vec2.py:157: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(


/root/audio/mhubert/venv/lib/python3.10/site-packages/transformers/models/wav2vec2/processing_wav2vec2.py:157: UserWarning: `as_target_processor` is deprecated and will be removed in v5 of Transformers. You can process your labels by using the argument `text` of the regular `__call__` method (either in the same call as your audio inputs, or in a separate call.
  warnings.warn(
IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.

In [46]:
trainer.push_to_hub()

events.out.tfevents.1720638005.sciencebrick.3579461.1:   0%|          | 0.00/625k [00:00<?, ?B/s]

events.out.tfevents.1720637180.sciencebrick.3579461.0:   0%|          | 0.00/6.25k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/378M [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/5.11k [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/AigizK/training/commit/9515ed057312efdbd933737b5bb3d04ab16a7a69', commit_message='End of training', commit_description='', oid='9515ed057312efdbd933737b5bb3d04ab16a7a69', pr_url=None, pr_revision=None, pr_num=None)

In [47]:
tokenizer.push_to_hub("AigizK/mHuBERT-147-bashkort")

README.md:   0%|          | 0.00/17.7k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/AigizK/mHuBERT-147-bashkort/commit/e6f2ad28f7a01efaea1dbd21697268fea5771e32', commit_message='Upload tokenizer', commit_description='', oid='e6f2ad28f7a01efaea1dbd21697268fea5771e32', pr_url=None, pr_revision=None, pr_num=None)